In [4]:
# Section to load a random dataset to test the pipeline on.

import numpy as np

# Create random data.
seq_train = 1e1 * np.random.randn( 10, 11)
seq_test = 1e1 * np.random.randn( 5, 11)

# Randomly select labels, 0 or 1.
seq_train[:,0] = np.random.randint(0,2, size=(seq_train.shape[0],))
seq_test[:,0] = np.random.randint(0,2, size=(seq_test.shape[0],))

# Set data and target matrices for train and test sets.
seq_train_X = seq_train[:,1:]
seq_train_y = seq_train[:,0]
seq_test_X = seq_test[:,1:]
seq_test_y = seq_test[:,0]

In [5]:
# Section to import sequential kernel SVC classifier.

from sklearn.svm import SVC
from sklearn.model_selection import GridSearchCV, cross_val_score
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

import seqsvc as ssvc
reload(ssvc)

<module 'seqsvc' from 'seqsvc.pyc'>

In [3]:
# Running the estimator check.
from sklearn.utils.estimator_checks import check_estimator
check_estimator(ssvc.SeqSVC) # Passed

/Users/Sam/anaconda/lib/python2.7/site-packages/sklearn/utils/validation.py:429: DataConversionWarning: Data with input dtype int64 was converted to float64 by StandardScaler.
  warnings.warn(msg, _DataConversionWarning)


In [6]:
test_pipeline = Pipeline([('scaler',StandardScaler()), ('seqsvc',ssvc.SeqSVC(normalise=False))])
test_pipeline.fit(seq_train_X, seq_train_y)
test_pipeline.predict(seq_test_X)
test_pipeline.score(seq_test_X, seq_test_y)
print cross_val_score(test_pipeline, seq_test_X, seq_test_y)

[ 1.  0.  1.]


In [3]:
test_clf = ssvc.SeqSVC(cut_ord_pair=(8,2), preprocess='index', C=100)
test_clf.fit(seq_train_X, seq_train_y)
test_clf.predict(seq_test_X)
test_clf.score(seq_test_X, seq_test_y)
print cross_val_score(test_clf, seq_test_X, seq_test_y)

kernelsqizer.py:56: RuntimeWarning: overflow encountered in multiply
  B[m,0,0]=np.multiply(K,(K3shifted2+1))
kernelsqizer.py:61: RuntimeWarning: invalid value encountered in multiply
  B[m,d,0]=np.divide(1,(d+1))*K*K2shifted
kernelsqizer.py:66: RuntimeWarning: invalid value encountered in multiply
  B[m,0,d]=np.divide(1,(d+1))*K*K4shifted_
kernelsqizer.py:69: RuntimeWarning: invalid value encountered in multiply
  B[m,d,d_]+=np.divide(1,((d+1)*(d_+1)))*K*B[m-1,d-1,d_-1]
/Users/Sam/anaconda/lib/python2.7/site-packages/sklearn/model_selection/_split.py:581: Warning: The least populated class in y has only 2 members, which is too few. The minimum number of groups for any class cannot be less than n_splits=3.
  % (min_groups, self.n_splits)), Warning)


[ 0.5  0.5  0. ]


In [7]:
def simplexGenerator(var_list):
    """For a decreasing list of values [a_0, ..., a_{n-1}], this function
    returns a list of tuples (a_i, a_j) where i <= j."""
    var_list = np.sort(var_list)[::-1]
    simplex = []
    for i in range(len(var_list)):
        for j in range(i, len(var_list)):
            simplex.append(tuple([var_list[i], var_list[j]]))

    return simplex

cut_ord_dom=2*np.arange(1,5)
Cs=np.logspace(-4,2,num=4,base=2.0)
params = dict( seqsvc__cut_ord_pair=simplexGenerator(cut_ord_dom), seqsvc__C=Cs.tolist(), seqsvc__preprocess=[0,'index'])
# params = dict( cut_ord_pair=simplexGenerator(cut_ord_dom), C=Cs.tolist(), gamma=Cs.tolist(),scale=Cs.tolist())
grid = GridSearchCV(test_pipeline, param_grid=params, n_jobs=-1, scoring='accuracy')

In [ ]:
grid.fit(seq_train_X, seq_train_y)

In [5]:
print grid.best_estimator_
print grid.best_estimator_.score(seq_test_X, seq_test_y)

SeqSVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
    cut_ord_pair=(8, 8), decision_function_shape=None, degree=3, gamma=1.0,
    kernel='rbf', max_iter=-1, n_iter_=1, normalise=True, preprocess=0,
    probability=False, random_state=None, scale=1.0, shrinking=True,
    tol=0.001, verbose=False)
1.0
